# xarray-einstats for ArviZ

In [1]:
# needs dask_einops branch of xarray-einstats
from xarray_einstats.einops import raw_rearrange
from xarray_einstats import stats
import einops
import scipy
import arviz as az
import numpy as np
import xarray as xr

xarray-einstats versions of rhat. They work on DataArrays (and can be applied to Datasets with `.map`) of _any_ number of dimensions as long as there is a `chain` and a `draw` dimension (like in ArviZ, their actual order doesn't matter though).

In [2]:
def _backtransform_ranks(da, c=3 / 8):  # pylint: disable=invalid-name
    """Backtransformation of ranks.
    
    Parameters
    ----------
    da : xr.DataArray
        Ranks array. It must have dimensions named `chain` and `draw`
    c : float
        Fractional offset. Defaults to c = 3/8 as recommended by Blom (1958).
        
    Returns
    -------
    xr.DataArray
    
    References
    ----------
    Blom, G. (1958). Statistical Estimates and Transformed Beta-Variables. Wiley; New York.
    """
    size = len(da.chain) * len(da.draw)
    return (da - c) / (size - 2 * c + 1)


def _z_scale(da, **kwargs):
    """Calculate z_scale.
    
    Parameters
    ----------
    da : xr.DataArray
        Input array. It must have dimensions named `chain` and `draw`

    Returns
    -------
    xr.DataArray
    """
    kwargs = kwargs.copy()
    if kwargs.get("dask", None) == "allowed":
        # scipy doesn't support dask properly, so even if we use dask="allowed" or dask directly
        # for everything else we need to force "parallelized" mode here
        kwargs["dask"] = "parallelized"
    rank = stats.rankdata(da, dims=("chain", "draw"), method="average", **kwargs)
    rank = _backtransform_ranks(rank)
    norm_dist = stats.XrContinuousRV(scipy.stats.norm)
    return norm_dist.ppf(rank, apply_kwargs=kwargs)


def _split_chains(da, **kwargs):
    """Split and stack chains."""
    half = len(da.draw) // 2
    if kwargs.get("dask", None) == "parallelized":
        # here we force dask="allowed" because einops doesn't play well with parallelized mode
        kwargs["dask"] = "allowed"
    return raw_rearrange(
        da, 
        "(d1 d2)=draw -> (chain d1)=c2 d2", 
        d2=half, 
        **kwargs
    ).rename(d2="draw", c2="chain")


def _z_fold(da, **kwargs):
    """Fold and z-scale values."""
    da = abs(da - da.median(("chain", "draw")))
    da = _z_scale(da, **kwargs)
    return da


def _rhat(da, **kwargs):
    """Compute the rhat for an n-D DataArray."""
    num_samples = len(da.draw)

    # Calculate chain mean
    chain_mean = da.mean("draw")
    # Calculate chain variance
    chain_var = da.var("draw", ddof=1)
    # Calculate between-chain variance
    between_chain_variance = num_samples * chain_mean.var("chain", ddof=1)
    # Calculate within-chain variance
    within_chain_variance = chain_var.mean("chain")
    # Estimate of marginal posterior variance
    rhat_value = np.sqrt(
        (between_chain_variance / within_chain_variance + num_samples - 1) / (num_samples)
    )
    return rhat_value


def _rhat_rank(da, **kwargs):
    """Compute the rank normalized rhat for an n-D DataArray.
    
    Computation follows https://arxiv.org/abs/1903.08008
    """
    split_da = _split_chains(da, **kwargs)
    rhat_bulk = _rhat(_z_scale(split_da, **kwargs))

    rhat_tail = _rhat(_z_fold(split_da, **kwargs))

    rhat_rank = xr.where(rhat_bulk > rhat_tail, rhat_bulk, rhat_tail)
    return rhat_rank

def rhat_einstats(ds, method="rank", **kwargs):
    func_map = {
        "identity": _rhat, 
        "rank": _rhat_rank
    }
    if method not in func_map:
        raise ValueError("method not recognized")
    rhat_func = func_map[method]
    if isinstance(ds, xr.Dataset):
        return ds.map(rhat_func, **kwargs)
    if isinstance(ds, xr.DataArray):
        return rhat_func(ds, **kwargs)

## Compare to current performance

In [3]:
post = az.load_arviz_data("centered_eight").posterior
%timeit rhat_einstats(post)
%timeit az.rhat(post)

34.6 ms ± 763 µs per loop (mean ± std. dev. of 7 runs, 10 loops each)
13 ms ± 383 µs per loop (mean ± std. dev. of 7 runs, 1 loop each)


For very small Datasets/DataArrays, it is slower than the current implementation. I think this is because
the main overhead when operating with xarray objects is the use of `apply_ufunc` which aligns and dispatches
the array operation on the xarray one, taking dims and coords into account.

In our current implementation, everything is implemented as array functions that work on 2d input only.
We then use `_make_ufunc` to loop over all 2d `chain, draw` chunks and apply that function. `apply_ufunc` is
called only once on that loop based ufunc.

This alternative uses xarray and xarray-einstats directly, so there are now many function calls happening
via `apply_ufunc`.

Both times are perfectly fast, and I don't think performance at this scale should be a concern. When the actual computation starts to be noticeable, this overhead effect is negligible and the xarray-einstats approach
scales much better. It is already faster on datasets of sizes similar to the radon dataset:

In [4]:
post = az.load_arviz_data("radon").posterior
%timeit rhat_einstats(post)
%timeit az.rhat(post)

280 ms ± 4.24 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
322 ms ± 1.84 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


## Dask integration and further scaling properties
Note: the class below is for `xarray_einstats.einops` to work correctly with dask backed xarrays.
As you saw, I use einops to split the chains. This can be added to xarray-einstats.

In [5]:
class DaskBackend(einops._backends.AbstractBackend):
    """ Base backend class, major part of methods are only for debugging purposes. """
    framework_name = "dask"

    def is_appropriate_type(self, tensor):
        """ helper method should recognize tensors it can handle """
        return isinstance(tensor, dask.array.core.Array)

    def from_numpy(self, x):
        raise dask.array.array(x)

    def to_numpy(self, x):
        raise x.compute()

    def arange(self, start, stop):
        # supplementary method used only in testing, so should implement CPU version
        raise dask.array.arange(start, stop)
        
    def stack_on_zeroth_dimension(self, tensors: list):
        return dask.array.stack(tensors)

    def tile(self, x, repeats):
        return dask.array.tile(x, repeats)

    def is_float_type(self, x):
        return x.dtype in ('float16', 'float32', 'float64', 'float128')

    def add_axis(self, x, new_position):
        return dask.array.expand_dims(x, new_position)

### Out of memory computation
`az.rhat` is one of the functions that already supports dask in ArviZ, so this would not make something
new possible with arviz, but I think that this approach of computation more integrated with xarray can
be applied to other functions and will be easier for dask integration with all stats and diagnostics.

The first step is showing that both `rhat_einstats` defined here and `az.rhat` can compute rhat on a ~15Gb dataset
from my 8Gb RAM laptop. I have used ~100MB chunks to allow Dask to store multiple chunks in memory while I use the computer and use the browser. Python only has 3-4Gb available to use. It would probably be a bit faster to use slightly larger chunks but that should affect all methods in a similar way.

In [6]:
import dask
import time

data = dask.array.random.normal(size=(4, 1000, 600_000), chunks={2: 3000})
post_dask = az.from_dict({"mu": data}, dims={"mu": ["obs_id"]}).posterior
data

dask.array<normal, shape=(4, 1000, 600000), dtype=float64, chunksize=(4, 1000, 3000), chunktype=numpy.ndarray>

In [7]:
s = time.time()
aux = rhat_einstats(post_dask, method="identity", dask="allowed").compute()
print(time.time() - s)
aux

37.907243967056274


<xarray.Dataset>
Dimensions:  (obs_id: 600000)
Coordinates:
  * obs_id   (obs_id) int64 0 1 2 3 4 5 ... 599995 599996 599997 599998 599999
Data variables:
    mu       (obs_id) float64 1.0 1.0 1.0 0.9998 ... 0.9997 0.9996 1.0 1.0

In [8]:
az.Dask.enable_dask(dask_kwargs={"dask": "parallelized"})
s = time.time()
aux = az.rhat(post_dask, method="identity").compute()
print(time.time() - s)
aux

arviz - WARNING - Shape validation failed: input_shape: (1, 1), minimum_shape: (chains=2, draws=4)


117.21799111366272


<xarray.Dataset>
Dimensions:  (obs_id: 600000)
Coordinates:
  * obs_id   (obs_id) int64 0 1 2 3 4 5 ... 599995 599996 599997 599998 599999
Data variables:
    mu       (obs_id) float64 1.0 1.0 1.0 0.9998 ... 0.9997 0.9996 1.0 1.0

We see that both work and give the same exact result. The current dask="parallelized" version is significantly slower, even with numba optimizations and even if the scipy part of the xarray-einstats implementation is also using dask="parallelized". Using dask="allowed" whenever possible allows dask to optimize much more the computation graph.

### Parallelized and optimized computation
Note: my idea was to run the comparisons below (except the first case) on `post_dask`, but it took very long and I
wasn't patient enough. So we compare with this dataset below with 6 chunks only. Doing that also has the side advantage of comparing numpy/in memory computation to dask parallelization and show it can even be useful on
data that fits in memory if the computations are expensive.

This section therefore shows again the `rhat_einstats` implementation but it is mostly an overview on the multiple
optimizations available in ArviZ right now side by side with this proposed change.

In [9]:
ds = post_dask.sel(obs_id=np.arange(18_000))
ds.mu.data

dask.array<getitem, shape=(4, 1000, 18000), dtype=float64, chunksize=(4, 1000, 3000), chunktype=numpy.ndarray>

#### `rhat_einstats`
##### In memory computation

In [10]:
s = time.time()
aux = rhat_einstats(ds.compute(), method="rank")
print(time.time() - s)

32.68025016784668


(note that above we computed rhat on 200 chunks instead of 6 chunks in 37 seconds, this should be an indicator on how good Dask is at parallelizing and optimizing the computational graph)

##### Distributed computing

In [11]:
s = time.time()
aux = rhat_einstats(ds, method="rank", dask="allowed").compute()
print(time.time() - s)

20.209238529205322


#### `az.rhat`
##### Dask + Numba

In [12]:
az.Dask.enable_dask(dask_kwargs={"dask": "parallelized"})
az.Numba.enable_numba()
s = time.time()
aux = az.rhat(ds, method="rank").compute()
print(time.time() - s)

53.61592626571655


##### Dask only

In [13]:
az.Dask.enable_dask(dask_kwargs={"dask": "parallelized"})
az.Numba.disable_numba()
s = time.time()
aux = az.rhat(ds, method="rank").compute()
print(time.time() - s)

61.22139835357666


##### Numba only (in memory computation)

In [14]:
az.Dask.disable_dask()
az.Numba.enable_numba()
s = time.time()
aux = az.rhat(ds.compute(), method="rank")
print(time.time() - s)

35.30549097061157


##### No optimizations (in memory computation)

In [15]:
az.Dask.disable_dask()
az.Numba.disable_numba()
s = time.time()
aux = az.rhat(ds.compute(), method="rank")
print(time.time() - s)

38.57915735244751


### Summary

There might be room for some further optimizations in `rhat_einstats` using Numba maybe, but even without them,
it outperforms the current implementation in all relevant cases.

Moreover, in my opinion, the code is simpler and easier to understand. It doesn't need `_make_ufunc` nor `wrap_xarray_ufunc` wrappers, it doesn't have `if numba` statements (that also need duplicated testing because it is a manual 2nd implementation and sometimes it doesn't return the same result) and it doesn't need a dask activation class nor dask compatible alternatives.

## Bonus: computation graph!
(needs to be right clicked and downloaded or opened on a new tab)

In [16]:
rhat_einstats(ds, method="rank", dask="allowed").mu.data.visualize()

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.953832 to fit
